In [1]:
import pandas as pd
import csv
import re
import warnings
import time 
warnings.filterwarnings('ignore')

In [2]:
file = "big_df.csv"  #large file for production
#file = "small_R_df.csv"       #small file for development
df = pd.read_csv('private/'+file, delimiter='|', encoding='latin-1')

In [3]:
#### stripping HTML tags ####
p = '<.*?>'
for col in df.columns:
    df[col] = df[col].replace(p, '', regex=True)

In [4]:
# splitting categories into main and sub, dropping non-Book main categories #
regex = r"\/(.*?)\/.*"

df['sub_cat'] = df['categoryPath'].str.extract(regex) # sub categories, one level below Books.
df['main_cat'] = df['categoryPath'].astype(str).str[:5] 
df = df[df.main_cat == 'Books'] #dropping non-Book categories

# drop rows missing critical data #
df = df.dropna(axis=0, how='any', subset=['longDn', 'sub_cat','name'])
df.isnull().sum().sort_values(ascending=False)

model           241307
parentItemId      3826
itemId            3375
shortDn            202
main_cat             0
sub_cat              0
catNode              0
longDn               0
categoryPath         0
name                 0
dtype: int64

In [5]:
print("There are " + str(len(df.sub_cat.value_counts())) + " categories of books.")
counts = df['sub_cat'].value_counts()
threshold = 100
print(str(len(counts[counts>threshold])) + " categories have more than " + str(threshold) +" books.")

There are 74 categories of books.
56 categories have more than 100 books.


In [6]:
Top_40_cats = df.sub_cat.value_counts().iloc[:39].index.tolist()

#df.sub_cat.value_counts().iloc[30:40]
print(df.sub_cat.value_counts().iloc[:39])


Business & Money Books                      20751
Children's & Kids' Books                    19802
Medical Books                               19238
History Books                               16723
Education Books                             14108
Computers & Technology Books                12785
Biographies & Memoirs                       10257
Sports & Outdoor Books                      10054
Law Books                                    9635
Political Books                              9273
Self-Help Books                              7097
Health & Wellness Books                      6852
Crafts & Hobbies Books                       6473
Mathematics Books                            6387
Philosophy Books                             6110
Travel Books                                 5810
Language Arts & Disciplines Books            5767
Reference Books                              5670
Foreign Language Study & Reference Books     5547
Teen & Young Adult Books                     5358


In [7]:
# Only keep records for top n populated categories (drop sparsely populated categories)
df = df.loc[df['sub_cat'].isin(Top_40_cats)]

In [77]:
df.sub_cat.value_counts().tail(n=30)

Political Books                             9273
Self-Help Books                             7097
Health & Wellness Books                     6852
Crafts & Hobbies Books                      6473
Mathematics Books                           6387
Philosophy Books                            6110
Travel Books                                5810
Language Arts & Disciplines Books           5767
Reference Books                             5670
Foreign Language Study & Reference Books    5547
Teen & Young Adult Books                    5358
Cookbooks, Food & Wine                      5031
Study Aids & Test Prep Books                3846
Humor Books                                 3491
Comic Books & Graphic Novels                3206
Literature & Fiction Books                  3163
Arts & Entertainment Books                  2570
Religion & Spirituality Books               2515
Psychology & Social Science Books           2336
Science & Nature Books                      1930
Libros en Espanol   

In [8]:
df.sub_cat.value_counts().iloc[:39].index.tolist()

#df.sub_cat.value_counts().iloc[30:40]
print(df.sub_cat.value_counts().iloc[:39])


Business & Money Books                      20751
Children's & Kids' Books                    19802
Medical Books                               19238
History Books                               16723
Education Books                             14108
Computers & Technology Books                12785
Biographies & Memoirs                       10257
Sports & Outdoor Books                      10054
Law Books                                    9635
Political Books                              9273
Self-Help Books                              7097
Health & Wellness Books                      6852
Crafts & Hobbies Books                       6473
Mathematics Books                            6387
Philosophy Books                             6110
Travel Books                                 5810
Language Arts & Disciplines Books            5767
Reference Books                              5670
Foreign Language Study & Reference Books     5547
Teen & Young Adult Books                     5358


In [9]:
#R_data_for_LDA = df
#R_data_for_LDA.to_csv('private/py_export_'+file, sep='|')

# Preparing Corpus and BOW for LDA Topic Modeling with Gensim
#### reference used: https://www.machinelearningplus.com/nlp/topic-modeling-gensim-python/

In [10]:
import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

import nltk; nltk.download('stopwords')
#!python3 -m spacy download en

[nltk_data] Error loading stopwords: <urlopen error [Errno 11001]
[nltk_data]     getaddrinfo failed>


False

In [11]:
import re
import numpy as np
import pandas as pd
from pprint import pprint

import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
import spacy

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
%matplotlib inline

# Enable logging for gensim - optional
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\decomposition\nmf.py:972: DeprecationWarning: invalid escape sequence \s
  """
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\decomposition\nmf.py:1186: DeprecationWarning: invalid escape sequence \s
  """
C:\ProgramData\Anaconda3\lib\site-packages\sklearn\manifold\t_sne.py:420: DeprecationWarning: invalid escape sequence \s
  """


In [35]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
stop_words.extend(['book'])

In [13]:
print(df.sub_cat.unique())

['Arts & Entertainment Books' "Children's & Kids' Books"
 'Business & Money Books' 'Cookbooks, Food & Wine'
 'Crafts & Hobbies Books' 'Literature & Fiction Books'
 'Religion & Spirituality Books' 'Dieting & Fitness Books'
 'Study Aids & Test Prep Books' 'Health & Wellness Books'
 'Biographies & Memoirs' 'Reference Books' 'Humor Books'
 'Libros en Espanol' 'Computers & Technology Books'
 'Comic Books & Graphic Novels' 'Teen & Young Adult Books' 'Medical Books'
 'Self-Help Books' 'History Books' 'True Crime Books'
 'Psychology & Social Science Books' 'House, Home & Gardening Books'
 'Travel Books' 'Education Books' 'Engineering & Transportation Books'
 'Science & Nature Books' 'Language Arts & Disciplines Books' 'Law Books'
 'Foreign Language Study & Reference Books' 'Mathematics Books'
 'Political Books' 'Philosophy Books' 'Sports & Outdoor Books'
 'Language Arts & Disciplines' 'Business & Money' 'Nonfiction' 'History'
 'Law']


In [32]:
data = df.longDn.values.tolist()

In [33]:
# converting contractions
data = [re.sub("won't","will not", sent) for sent in data]
data = [re.sub("can't","can not", sent) for sent in data]
data = [re.sub("n't","not", sent) for sent in data]
data = [re.sub("\'ll"," will", sent) for sent in data]
data = [re.sub("\'re"," are", sent) for sent in data]
data = [re.sub("\'ve"," have", sent) for sent in data]

# removing any single quotes
data = [re.sub("\'", " ", sent) for sent in data] 
# removing pipes to help with saving csv as pipe-delimited
data = [re.sub("\|", " ", sent) for sent in data]
# leave only letters and numbers (makes above lines redundant, but that's ok)
data = [re.sub("[^a-zA-Z0-9 ]", " ", sent) for sent in data]
# removing any extraneous spaces
data = [re.sub("\s+", " ", sent) for sent in data] #strip extra spaces

<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:16: DeprecationWarning: invalid escape sequence \s
<input>:12: DeprecationWarning: invalid escape sequence \|
<input>:16: DeprecationWarning: invalid escape sequence \s
<input>:12: DeprecationWarning: invalid escape sequence 

In [34]:
data[300]

'Robust DC Comics Roster Engage in epic match ups with a massive roster of DC Comics heroes and villains including Batman Cyborg The Flash Harley Quinn Nightwing Solomon Grundy Superman and Wonder Woman Master God Like Powers Unleash each character s unique super powers with individual move sets and environmental interactions Uncontainable Battles Fight through multi tiered fighting arenas by hurling opponents through buildings and launching them off cliffs Original DC Comics Saga Set in Iconic Environments Experience an authentic DC Comics storyline created in collaboration between NetherRealm Studios DC Entertainment and writers Justin Gray and Jimmy Palmiotti Players will discover and do battle in numerous iconic locales pulled from DC Comics lore Destructive Fighter in which the World is a Weapon Experience epic battles on a massive scale as players control the most powerful beings in the universe in destructible interactive environments Destroy elements of the world and use super 

In [36]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [37]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=50) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

# See trigram example
#print(trigram_mod[bigram_mod[data_words[4]]])

['dr_seuss', 'wonderfully', 'wise', 'oh', 'the', 'places', 'you', 'll', 'go', 'is', 'the', 'perfect', 'send', 'off', 'for', 'grads', 'from', 'nursery', 'school', 'high', 'school', 'college', 'and', 'beyond', 'from', 'soaring', 'to', 'high', 'heights', 'and', 'seeing', 'great', 'sights', 'to', 'being', 'left', 'in', 'lurch', 'on', 'prickle', 'ly', 'perch', 'dr_seuss', 'addresses', 'life', 'ups', 'and', 'downs', 'with', 'his', 'trademark', 'humorous', 'verse', 'and', 'illustrations', 'while', 'encouraging', 'readers', 'to', 'find', 'the', 'success', 'that', 'lies', 'within', 'in', 'starred_review', 'booklist', 'notes', 'seuss', 'message', 'is', 'simple', 'but', 'never', 'sappy', 'life', 'may', 'be', 'great', 'balancing_act', 'but', 'through', 'it', 'all', 'there', 'fun', 'to', 'be', 'done', 'perennial_favorite', 'and', 'perfect', 'gift', 'for', 'anyone', 'starting', 'new', 'phase', 'in', 'their', 'life']


In [38]:
start = time.time()
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

end = time.time()
print(end-start)

In [39]:
start = time.time()
data_words_nostops = remove_stopwords(data_words)
data_words_bigrams = make_bigrams(data_words_nostops)
nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

#print(data_lemmatized[:4])
end = time.time()
print(end-start)

C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr)).reshape(obj[b'shape'])
C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr))[0]
C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr)).reshape(obj[b'shape'])
C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr)).reshape(obj[b'shape'])
C:\ProgramData\Anaconda3\lib\site-pa

C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr)).reshape(obj[b'shape'])
C:\ProgramData\Anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  dtype=np.dtype(descr)).reshape(obj[b'shape'])


[['garth_brook', 'anthology'], ['perfect', 'gift', 'collector', 'new', 'reader', 'alike', 'present', 'breathtaking', 'special', 'edition', 'boxed_set', 'jharry', 'potter', 'sorcerer_stone', 'harry_potter', 'chamber', 'secret', 'harry_potter', 'prisoner', 'azkaban', 'harry_potter', 'goblet', 'fire', 'harry_potter', 'order', 'phoenix', 'harry_potter', 'half', 'blood', 'prince', 'harry_potter', 'deathly_hallow', 'isbn', 'series', 'harry', 'potterprimary', 'category', 'juvenile', 'fiction', 'fantasy', 'magic'], ['strengthsfinder', 'feature', 'new', 'upgrade', 'version', 'strengthsfinder', 'program', 'main', 'selling', 'point', 'mega', 'bestseller', 'discover', 'strength', 'million_copie', 'sell', 'access', 'new', 'upgrade', 'strengthsfinder', 'program', 'available', 'exclusively', 'opportunity', 'good', 'day', 'chance', 'often', 'natural', 'talent', 'go', 'untapped', 'cradle', 'cubicle', 'devote', 'time', 'fix', 'shortcoming', 'develop', 'strength', 'help', 'people', 'uncover', 'talent', '

In [40]:
start = time.time()

id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]
end = time.time()
print(end-start)

In [41]:
#reviewing term frequency
#[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:2]]

# Begin LDA Multicore Model

In [42]:
start = time.time()

lda_multicore_model = gensim.models.ldamulticore.LdaMulticore(~corpus=corpus,
                                           id2word=id2word,
                                           workers=3,
                                           num_topics=40, 
                                           random_state=100,
                                           eval_every=1,   # update_every = how often the model should be updated 
                                           chunksize=5000,  # chunksize = number of docs to be used in each training chunk
                                           passes=2,        # passes = total number of training passes
                                           #alpha='auto',
                                           per_word_topics=True)
end = time.time()
print(end-start)

297.54716086387634


In [45]:
pprint(lda_multicore_model.print_topics())
doc_lda = lda_multicore_model[corpus]

[(10,
  '0.034*"food" + 0.027*"recipe" + 0.013*"make" + 0.012*"eat" + 0.010*"cook" + '
  '0.009*"cookbook" + 0.008*"include" + 0.007*"meal" + 0.007*"easy" + '
  '0.007*"delicious"'),
 (39,
  '0.011*"book" + 0.007*"image" + 0.007*"edition" + 0.007*"classic" + '
  '0.006*"imperfection" + 0.006*"zen" + 0.005*"text" + 0.005*"reproduction" + '
  '0.005*"nail" + 0.005*"quality"'),
 (24,
  '0.007*"jewish" + 0.006*"addiction" + 0.006*"world" + 0.006*"people" + '
  '0.006*"right" + 0.005*"time" + 0.004*"make" + 0.004*"country" + 0.004*"jew" '
  '+ 0.004*"first"'),
 (21,
  '0.023*"game" + 0.008*"play" + 0.004*"make" + 0.004*"young" + 0.004*"world" '
  '+ 0.004*"find" + 0.004*"new" + 0.003*"princess" + 0.003*"royal" + '
  '0.003*"learn"'),
 (15,
  '0.008*"provide" + 0.007*"research" + 0.006*"theory" + 0.006*"use" + '
  '0.005*"system" + 0.005*"law" + 0.005*"health" + 0.005*"issue" + '
  '0.005*"approach" + 0.005*"development"'),
 (38,
  '0.018*"plant" + 0.014*"garden" + 0.011*"collection" + '
  '

In [46]:
start = time.time()
# Compute Perplexity
print('\nPerplexity: ', lda_multicore_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_multicore_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)
end = time.time()
print(end-start)


Perplexity:  -8.653923361102978

Coherence Score:  0.5232047439787118


In [29]:
pprint(lda_multicore_model.print_topics())
doc_lda = lda_multicore_model[corpus]

[(15,
  '0.009*"new" + 0.006*"history" + 0.005*"year" + 0.005*"business" + '
  '0.005*"life" + 0.005*"war" + 0.004*"american" + 0.004*"become" + '
  '0.003*"man" + 0.003*"state"'),
 (27,
  '0.020*"la" + 0.010*"para" + 0.008*"que" + 0.007*"con" + 0.006*"como" + '
  '0.005*"por" + 0.005*"los" + 0.004*"una" + 0.003*"sobre" + 0.003*"new"'),
 (34,
  '0.006*"horse" + 0.005*"map" + 0.005*"time" + 0.005*"new" + 0.004*"volume" + '
  '0.004*"book" + 0.004*"write" + 0.004*"great" + 0.004*"city" + '
  '0.003*"world"'),
 (39,
  '0.008*"work" + 0.007*"new" + 0.007*"include" + 0.006*"guide" + '
  '0.006*"imperfection" + 0.006*"publish" + 0.005*"part" + 0.005*"use" + '
  '0.005*"may" + 0.005*"print"'),
 (22,
  '0.006*"know" + 0.006*"new" + 0.005*"get" + 0.005*"game" + 0.004*"time" + '
  '0.004*"life" + 0.004*"world" + 0.004*"include" + 0.003*"team" + '
  '0.003*"adventure"'),
 (13,
  '0.015*"health" + 0.007*"game" + 0.006*"author" + 0.005*"include" + '
  '0.004*"help" + 0.004*"care" + 0.004*"first" + 

In [48]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_multicore_model, corpus, id2word)
vis

C:\ProgramData\Anaconda3\lib\site-packages\numexpr\cpuinfo.py:109: DeprecationWarning: invalid escape sequence \d
  nbits = re.compile('(\d+)bit').search(abits).group(1)
C:\ProgramData\Anaconda3\lib\site-packages\numexpr\cpuinfo.py:662: DeprecationWarning: invalid escape sequence \s
  "\s+stepping\s+(?P<STP>\d+)", re.IGNORECASE)


PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
30     9.541323        1       1 -0.128403 -0.137159
15     8.779309        1       2 -0.162220  0.163129
11     7.582428        1       3 -0.090346 -0.152572
17     5.926909        1       4 -0.166280  0.170767
20     5.522479        1       5 -0.137588 -0.013381
28     5.116127        1       6 -0.115745 -0.005409
13     4.825443        1       7 -0.123281  0.127019
6      4.329328        1       8 -0.064187 -0.189768
8      3.314811        1       9 -0.107063  0.164314
31     3.278664        1      10 -0.069700 -0.111692
2      3.273857        1      11 -0.134089  0.183612
3      2.884887        1      12 -0.102240  0.020257
12     2.796902        1      13 -0.110612  0.104091
19     2.551021        1      14 -0.101827  0.098675
10     2.469301        1      15 -0.021996 -0.008580
34     2.441831        1      16 -0.066546  0.087762
9      2.213564        1      17 -0.090436 -0.001980
26     2.166171        1      18 -0.133841  0.066716
0      2.060862        1      19 -0.016851 -0.076327
32     2.060176        1      20  0.309552  0.103480
29     2.018830        1      21 -0.029372 -0.136792
18     1.756654        1      22  0.224183  0.141455
36     1.494894        1      23 -0.025588 -0.033561
35     1.260312        1      24 -0.021272 -0.108394
5      1.155716        1      25 -0.000026 -0.015017
25     1.069255        1      26 -0.042876 -0.069706
24     0.997794        1      27 -0.054600 -0.066859
21     0.846982        1      28 -0.007433 -0.102238
33     0.750932        1      29  0.247862  0.080346
7      0.733539        1      30 -0.033759 -0.018758
27     0.684675        1      31  0.034502 -0.121060
23     0.653876        1      32  0.236779  0.044682
38     0.582049        1      33  0.104327 -0.070663
22     0.579444        1      34 -0.015672 -0.002154
37     0.501252        1      35  0.058354 -0.102146
4      0.431370        1      36  0.224893  0.005049
1      0.362188        1      37  0.097813 -0.034509
16     0.358924        1      38  0.176655 -0.020950
39     0.328901        1      39  0.187128  0.009497
14     0.297022        1      40  0.271803  0.028823, topic_info=      Category          Freq           Term         Total  loglift  logprob
term                                                                       
863    Default  25518.000000       business  25518.000000  30.0000  30.0000
1536   Default  16211.000000            die  16211.000000  29.0000  29.0000
9657   Default  13198.000000            der  13198.000000  28.0000  28.0000
9661   Default  12906.000000            und  12906.000000  27.0000  27.0000
851    Default  17840.000000           test  17840.000000  26.0000  26.0000
78     Default  43785.000000          guide  43785.000000  25.0000  25.0000
590    Default  50579.000000           work  50579.000000  24.0000  24.0000
709    Default  15515.000000         health  15515.000000  23.0000  23.0000
703    Default  12978.000000           food  12978.000000  22.0000  22.0000
2398   Default  10262.000000             la  10262.000000  21.0000  21.0000
831    Default  24542.000000       practice  24542.000000  20.0000  20.0000
378    Default  24900.000000        student  24900.000000  19.0000  19.0000
3595   Default   9424.000000           exam   9424.000000  18.0000  18.0000
2225   Default   9048.000000            map   9048.000000  17.0000  17.0000
1486   Default   8753.000000         recipe   8753.000000  16.0000  16.0000
600    Default  21226.000000          child  21226.000000  15.0000  15.0000
24     Default  67827.000000            new  67827.000000  14.0000  14.0000
560    Default  19937.000000       question  19937.000000  13.0000  13.0000
11     Default  24035.000000        edition  24035.000000  12.0000  12.0000
1320   Default   9980.000000            war   9980.000000  11.0000  11.0000
130    Default  48058.000000            use  48058.000000  

In [ ]:
- intentional fail to prevent subsequent code to run -
fail.

# Begin LDA Model

In [43]:

start = time.time()
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=40, 
                                           random_state=100,
                                           #update_every=1,   # update_every = how often the model should be updated 
                                           chunksize=5000,    # chunksize = number of docs to be used in each training chunk
                                           passes=2,
                                           #alpha='auto',
                                           per_word_topics=True)
end = time.time()
print(end-start)


1530414258.3731391
1530415127.724409
869.3512699604034


In [44]:
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(16,
  '0.054*"die" + 0.053*"und" + 0.050*"der" + 0.010*"den" + 0.010*"eine" + '
  '0.010*"das" + 0.010*"fur" + 0.009*"ist" + 0.008*"auf" + 0.008*"be"'),
 (13,
  '0.016*"student" + 0.015*"include" + 0.014*"research" + 0.014*"chapter" + '
  '0.014*"study" + 0.012*"theory" + 0.011*"science" + 0.011*"text" + '
  '0.011*"provide" + 0.010*"analysis"'),
 (0,
  '0.026*"book" + 0.023*"imperfection" + 0.020*"may" + 0.019*"work" + '
  '0.017*"original" + 0.017*"historical" + 0.016*"classic" + 0.016*"find" + '
  '0.016*"rare" + 0.016*"remain"'),
 (30,
  '0.025*"life" + 0.010*"make" + 0.009*"time" + 0.009*"people" + 0.008*"know" '
  '+ 0.008*"live" + 0.008*"get" + 0.007*"take" + 0.007*"way" + 0.007*"year"'),
 (5,
  '0.016*"french" + 0.013*"part" + 0.012*"africa" + 0.012*"travel" + '
  '0.012*"europe" + 0.011*"france" + 0.010*"museum" + 0.010*"publish" + '
  '0.010*"japanese" + 0.010*"country"'),
 (34,
  '0.085*"work" + 0.020*"edition" + 0.019*"important" + 0.018*"part" + '
  '0.017*"english" + 0.

In [47]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -9.030667364663111

Coherence Score:  0.5307975222715445


In [49]:
start = time.time()
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)

end = time.time()
print(end-start)
vis

PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
30     13.899226        1       1 -0.283695 -0.097807
28      8.979142        1       2 -0.272768 -0.039775
15      7.684340        1       3 -0.273044  0.212987
20      7.644435        1       4 -0.267351  0.155308
13      6.084368        1       5 -0.226168  0.169547
31      5.603837        1       6 -0.210321 -0.110136
3       4.903196        1       7 -0.229101  0.106620
11      4.230517        1       8 -0.177652 -0.225990
26      3.765106        1       9 -0.180149  0.114691
14      3.329988        1      10 -0.138183 -0.256444
6       3.144576        1      11 -0.158224 -0.199318
16      2.010964        1      12  0.126565  0.030135
18      1.940254        1      13  0.135343  0.040313
36      1.934104        1      14 -0.057097 -0.115889
24      1.844967        1      15 -0.020987  0.042245
17      1.841125        1      16 -0.115744  0.153872
9       1.634623        1      17 -0.059867  0.045168
0       1.582078        1      18  0.000367 -0.016230
32      1.581633        1      19 -0.070799 -0.105084
5       1.483851        1      20  0.028693 -0.040478
35      1.381936        1      21 -0.024136 -0.020891
12      1.321861        1      22 -0.024803  0.151706
10      1.291243        1      23  0.138535  0.045810
34      1.047399        1      24  0.056979  0.028946
23      0.972813        1      25  0.075651 -0.130596
4       0.838038        1      26  0.154594  0.038749
38      0.736016        1      27  0.119254  0.008435
29      0.717011        1      28  0.095941 -0.057108
27      0.690037        1      29  0.111025 -0.103049
25      0.635761        1      30  0.119336  0.005252
33      0.621839        1      31  0.166358  0.016525
19      0.599300        1      32  0.145835  0.010752
37      0.590183        1      33  0.149282 -0.030625
8       0.536752        1      34  0.142397  0.043414
1       0.514663        1      35  0.168463 -0.002014
7       0.497006        1      36  0.164175  0.049572
21      0.483389        1      37  0.170602  0.023715
2       0.479827        1      38  0.167630  0.016598
22      0.464897        1      39  0.173522  0.003170
39      0.457696        1      40  0.179542  0.037905, topic_info=       Category          Freq             Term         Total  loglift  logprob
term                                                                          
590     Default  53444.000000             work  53444.000000  30.0000  30.0000
863     Default  27442.000000         business  27442.000000  29.0000  29.0000
78      Default  41637.000000            guide  41637.000000  28.0000  28.0000
718     Default  42567.000000            learn  42567.000000  27.0000  27.0000
780     Default  40776.000000            story  40776.000000  26.0000  26.0000
1031    Default  14506.000000            woman  14506.000000  25.0000  25.0000
354     Default  22038.000000              man  22038.000000  24.0000  24.0000
1536    Default  16735.000000              die  16735.000000  23.0000  23.0000
851     Default  16907.000000             test  16907.000000  22.0000  22.0000
24      Default  66320.000000              new  66320.000000  21.0000  21.0000
11      Default  25066.000000          edition  25066.000000  20.0000  20.0000
9661    Default  13664.000000              und  13664.000000  19.0000  19.0000
158     Default  62799.000000             life  62799.000000  18.0000  18.0000
2857    Default  10238.000000            sport  10238.000000  17.0000  17.0000
9657    Default  12754.000000              der  12754.000000  16.0000  16.0000
703     Default  11807.000000             food  11807.000000  15.0000  15.0000
560     Default  18708.000000         question  18708.000000  14.0000  14.0000
847     Default  20792.000000            study  20792.000000  13.0000  13.0000
135     Default  46925.000000            world  46925.000000  12.0000  12.0000
831     Default  22869.000000 

# LDA Multicore model approach #2, fewer categories

In [69]:
start = time.time()
lda_model_2 = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=30, 
                                           random_state=100,
                                           eval_every=1,      # update_every = how often the model should be updated 
                                           chunksize=10000,    # chunksize = number of docs to be used in each training chunk
                                           passes=2,
                                           per_word_topics=True)
end = time.time()
print(end-start)

204.76681232452393


In [70]:
# Compute Perplexity
print('\nPerplexity: ', lda_model_2.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model_2, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -8.883864614819519

Coherence Score:  0.4452825313034552


In [71]:
start = time.time()
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model_2, corpus, id2word)

end = time.time()
print(end-start)
vis

464.9169855117798


PreparedData(topic_coordinates=            Freq  cluster  topics             x         y
topic                                                    
17     10.737969        1       1  4.515359e-02  0.114358
19      7.393533        1       2  7.797553e-02 -0.009678
27      6.878052        1       3  8.348925e-02 -0.143252
6       6.726040        1       4  3.857380e-02 -0.077748
20      6.593369        1       5  2.248494e-02  0.009995
15      5.761143        1       6  3.041182e-03  0.106870
26      5.552044        1       7  5.396670e-02  0.010645
2       3.947515        1       8 -1.268712e-03  0.083428
11      3.799010        1       9  4.325874e-02 -0.073758
0       3.728054        1      10  5.849806e-02 -0.062652
13      3.694675        1      11 -1.424620e-02  0.063881
10      3.587152        1      12 -1.251912e-02  0.023548
3       3.474605        1      13 -1.919819e-03  0.015057
7       3.213003        1      14  2.490068e-02  0.009787
21      2.300317        1      15  3.401319e-02 -0.004379
23      2.261541        1      16  1.897362e-02 -0.061963
1       2.175282        1      17 -2.803580e-01 -0.069189
18      2.148599        1      18 -2.882410e-02  0.081263
12      2.146558        1      19 -1.630919e-03  0.057764
25      1.762174        1      20  9.275460e-07  0.015535
22      1.703883        1      21 -1.899562e-02  0.054945
8       1.703254        1      22 -1.853327e-02  0.046761
5       1.607288        1      23  2.334612e-03  0.010338
24      1.526057        1      24  3.208608e-02 -0.046107
29      1.306816        1      25  3.564342e-03 -0.073200
28      1.181223        1      26  8.469767e-03  0.011115
9       0.908052        1      27 -1.128777e-02  0.007082
4       0.784566        1      28 -8.339655e-03 -0.031430
16      0.752232        1      29 -8.258938e-02 -0.019587
14      0.645994        1      30 -7.027248e-02 -0.049429, topic_info=     Category          Freq          Term         Total  loglift  logprob
term                                                                     
1536  Default  13916.000000           die  13916.000000  30.0000  30.0000
9657  Default  10981.000000           der  10981.000000  29.0000  29.0000
9661  Default  10855.000000           und  10855.000000  28.0000  28.0000
24    Default  68776.000000           new  68776.000000  27.0000  27.0000
130   Default  49336.000000           use  49336.000000  26.0000  26.0000
78    Default  36607.000000         guide  36607.000000  25.0000  25.0000
352   Default  55034.000000          make  55034.000000  24.0000  24.0000
590   Default  49175.000000          work  49175.000000  23.0000  23.0000
600   Default  28384.000000         child  28384.000000  22.0000  22.0000
158   Default  58369.000000          life  58369.000000  21.0000  21.0000
1486  Default  13175.000000        recipe  13175.000000  20.0000  20.0000
84    Default  52132.000000       include  52132.000000  19.0000  19.0000
378   Default  28602.000000       student  28602.000000  18.0000  18.0000
2398  Default   8126.000000            la   8126.000000  17.0000  17.0000
780   Default  38810.000000         story  38810.000000  16.0000  16.0000
86    Default  17328.000000      language  17328.000000  15.0000  15.0000
1031  Default  14296.000000         woman  14296.000000  14.0000  14.0000
718   Default  39556.000000         learn  39556.000000  13.0000  13.0000
703   Default  13736.000000          food  13736.000000  12.0000  12.0000
863   Default  27236.000000      business  27236.000000  11.0000  11.0000
135   Default  46160.000000         world  46160.000000  10.0000  10.0000
1312  Default  21323.000000          step  21323.000000   9.0000   9.0000
8587  Default   5347.000000  imperfection   5347.000000   8.0000   8.0000
148   Default  32364.000000          find  32364.000000   7.0000   7.0000
851   Default  16276.000000          test  16276.000000   6.0000   6.0000
71    Default  33360.000000         first  33360.000000   5.0000   5.0000
797   Default  20224.000000  

# Begin LDA Mallet

In [ ]:
from gensim.models.wrappers import LdaMallet

In [64]:
start = time.time()
# Download File: http://mallet.cs.umass.edu/dist/mallet-2.0.8.zip
mallet_path = "mallet-2.0.8/bin/" # update this path
ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=corpus, num_topics=20, id2word=id2word, workers=3)
end = time.time()
print(end-start)

CalledProcessError: Command 'mallet-2.0.8/bin import-file --preserve-case --keep-sequence --remove-stopwords --token-regex "\S+" --input C:\Users\BS\AppData\Local\Temp\421d0c_corpus.txt --output C:\Users\BS\AppData\Local\Temp\421d0c_corpus.mallet' returned non-zero exit status 1.

In [ ]:
start = time.time()
pprint(ldamallet.show_topics(formatted=False))

# Compute Coherence Score
coherence_model_ldamallet = CoherenceModel(model=ldamallet, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_ldamallet = coherence_model_ldamallet.get_coherence()
print('\nCoherence Score: ', coherence_ldamallet)
end = time.time()
print(end-start)

In [73]:
#redo of LDA model

start = time.time()
lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=40, 
                                           random_state=100,
                                           #update_every=1,   # update_every = how often the model should be updated 
                                           chunksize=5000,    # chunksize = number of docs to be used in each training chunk
                                           passes=2,
                                           #alpha='auto',
                                           per_word_topics=True)


pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)

end = time.time()
print(end-start)
vis

789.8060405254364


PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
15     9.356139        1       1 -0.078050 -0.132106
17     9.083819        1       2 -0.081230 -0.150216
30     6.512586        1       3 -0.051662  0.079994
11     6.455867        1       4 -0.046900  0.116920
19     5.937752        1       5 -0.074688  0.008146
20     5.315341        1       6 -0.050135  0.002754
0      4.116662        1       7 -0.046237  0.090273
13     3.810459        1       8 -0.041080 -0.064441
2      3.662748        1       9 -0.054134 -0.134428
7      3.301485        1      10 -0.046112 -0.036419
6      3.238219        1      11 -0.016799  0.080927
10     2.732191        1      12  0.000112 -0.029321
31     2.585917        1      13 -0.025566 -0.012609
3      2.374174        1      14 -0.022389 -0.019021
8      2.195399        1      15 -0.022079 -0.096164
29     2.185242        1      16 -0.020143  0.111184
26     2.156751        1      17 -0.055149 -0.034871
18     2.026996        1      18  0.047079 -0.095586
1      1.734829        1      19  0.350610 -0.042477
27     1.687991        1      20 -0.026078  0.124590
35     1.614398        1      21 -0.018127  0.049619
39     1.502245        1      22  0.057374  0.036195
28     1.431042        1      23 -0.037451 -0.014464
12     1.426890        1      24 -0.028340 -0.084101
5      1.251958        1      25 -0.027470  0.012178
23     1.080943        1      26  0.012317  0.107733
36     1.051440        1      27 -0.003358 -0.013113
4      1.026365        1      28  0.010312  0.043419
9      0.985319        1      29 -0.016066 -0.018994
25     0.964933        1      30 -0.020799 -0.020931
24     0.915711        1      31 -0.025928  0.053709
37     0.871670        1      32  0.005261  0.070962
21     0.861174        1      33 -0.019577  0.009070
33     0.822592        1      34  0.044283  0.030894
38     0.729487        1      35  0.018169  0.041659
34     0.677675        1      36  0.015159 -0.023746
22     0.630537        1      37 -0.003162 -0.025788
32     0.624742        1      38  0.055196  0.003916
14     0.608125        1      39  0.270766 -0.017597
16     0.452184        1      40  0.072072 -0.007748, topic_info=      Category          Freq          Term         Total  loglift  logprob
term                                                                      
590    Default  47341.000000          work  47341.000000  30.0000  30.0000
1536   Default  14701.000000           die  14701.000000  29.0000  29.0000
9657   Default  11609.000000           der  11609.000000  28.0000  28.0000
9661   Default  11455.000000           und  11455.000000  27.0000  27.0000
24     Default  69853.000000           new  69853.000000  26.0000  26.0000
130    Default  48348.000000           use  48348.000000  25.0000  25.0000
78     Default  39451.000000         guide  39451.000000  24.0000  24.0000
780    Default  35946.000000         story  35946.000000  23.0000  23.0000
2398   Default   9337.000000            la   9337.000000  22.0000  22.0000
158    Default  57132.000000          life  57132.000000  21.0000  21.0000
135    Default  45731.000000         world  45731.000000  20.0000  20.0000
352    Default  53000.000000          make  53000.000000  19.0000  19.0000
600    Default  24984.000000         child  24984.000000  18.0000  18.0000
84     Default  52279.000000       include  52279.000000  17.0000  17.0000
8587   Default   5800.000000  imperfection   5800.000000  16.0000  16.0000
863    Default  25532.000000      business  25532.000000  15.0000  15.0000
718    Default  37342.000000         learn  37342.000000  14.0000  14.0000
378    Default  27185.000000       student  27185.000000  13.0000  13.0000
344    Default  16267.000000     important  16267.000000  12.0000  12.0000
148    Default  33039.000000          find  33039.000000  11.0000  11.0000
709    Default  16087.000000        health  16087.000000  10.0000  10.0000
703   

In [74]:
#redo of LDA multicore model. Should be same as above

start = time.time()
lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=40, 
                                           random_state=100,
                                           #update_every=1,   # update_every = how often the model should be updated 
                                           chunksize=5000,    # chunksize = number of docs to be used in each training chunk
                                           passes=2,
                                           #alpha='auto',
                                           per_word_topics=True)


pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)

end = time.time()
print(end-start)
vis

794.335693359375


PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
15     10.440599        1       1  0.081645  0.115930
17      8.406440        1       2  0.083811  0.147403
11      7.117528        1       3  0.039109 -0.110712
30      6.589091        1       4  0.047768 -0.073695
19      5.569254        1       5  0.072975 -0.001572
20      5.196862        1       6  0.047785  0.000952
13      3.994071        1       7  0.041367  0.068480
2       3.762646        1       8  0.058226  0.126526
0       3.481446        1       9  0.036440 -0.085110
6       3.338112        1      10  0.012811 -0.082842
7       3.044660        1      11  0.046188  0.026790
10      2.760803        1      12  0.006350  0.024496
8       2.331488        1      13  0.021854  0.084745
3       2.223810        1      14  0.021620  0.014660
31      2.206067        1      15  0.022638  0.010278
18      2.026735        1      16 -0.030371  0.088535
26      2.012003        1      17  0.053819  0.035710
29      1.990027        1      18  0.010906 -0.105501
27      1.925642        1      19  0.019840 -0.123834
1       1.669455        1      20 -0.335651  0.054277
39      1.519690        1      21 -0.051928 -0.044479
35      1.500837        1      22  0.014338 -0.051512
5       1.465884        1      23  0.028113 -0.010199
12      1.440638        1      24  0.029520  0.082796
28      1.270337        1      25  0.030341  0.015836
23      1.173926        1      26 -0.005464 -0.103292
4       1.144776        1      27 -0.009495 -0.044533
36      1.051694        1      28  0.004147  0.014149
25      0.997982        1      29  0.019542  0.019894
9       0.933816        1      30  0.013025  0.013773
24      0.910575        1      31  0.023388 -0.046508
37      0.900159        1      32 -0.006225 -0.067972
21      0.880228        1      33  0.018284 -0.008870
33      0.829300        1      34 -0.036180 -0.035161
34      0.744860        1      35 -0.003343  0.024536
38      0.733535        1      36 -0.018213 -0.041046
14      0.674254        1      37 -0.274636  0.026839
32      0.646391        1      38 -0.062171 -0.000703
22      0.621552        1      39  0.004698  0.029435
16      0.472830        1      40 -0.076872  0.011500, topic_info=      Category          Freq          Term         Total  loglift  logprob
term                                                                      
590    Default  46762.000000          work  46762.000000  30.0000  30.0000
1536   Default  14443.000000           die  14443.000000  29.0000  29.0000
9657   Default  11409.000000           der  11409.000000  28.0000  28.0000
9661   Default  11106.000000           und  11106.000000  27.0000  27.0000
24     Default  69869.000000           new  69869.000000  26.0000  26.0000
130    Default  49374.000000           use  49374.000000  25.0000  25.0000
78     Default  39548.000000         guide  39548.000000  24.0000  24.0000
780    Default  35403.000000         story  35403.000000  23.0000  23.0000
2398   Default   9206.000000            la   9206.000000  22.0000  22.0000
352    Default  54107.000000          make  54107.000000  21.0000  21.0000
600    Default  25608.000000         child  25608.000000  20.0000  20.0000
135    Default  45596.000000         world  45596.000000  19.0000  19.0000
158    Default  55266.000000          life  55266.000000  18.0000  18.0000
84     Default  52528.000000       include  52528.000000  17.0000  17.0000
378    Default  27981.000000       student  27981.000000  16.0000  16.0000
1031   Default  13177.000000         woman  13177.000000  15.0000  15.0000
718    Default  38740.000000         learn  38740.000000  14.0000  14.0000
8587   Default   5715.000000  imperfection   5715.000000  13.0000  13.0000
863    Default  25926.000000      business  25926.000000  12.0000  12.0000
1486   Default  11196.000000        recipe  11196.000000  11.0000  11.0000
851    Default  17836.000000          t

In [75]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=20, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        model = gensim.models.wrappers.LdaMallet(mallet_path, corpus=corpus, num_topics=num_topics, id2word=id2word)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values

start_time = time.time()
# Can take a long time to run.
model_list, coherence_values = compute_coherence_values(dictionary=id2word, corpus=corpus, texts=data_lemmatized, start=30, limit=45, step=3)

end = time.time()
print(end-start_time)

# Show graph
limit=45; start=30; step=3;
x = range(start, limit, step)
plt.plot(x, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence score")
plt.legend(("coherence_values"), loc='best')
plt.show()

# Print the coherence scores
for m, cv in zip(x, coherence_values):
    print("Num Topics =", m, " has Coherence Value of", round(cv, 4))

end = time.time()
print(end-start)

CalledProcessError: Command 'mallet-2.0.8/bin import-file --preserve-case --keep-sequence --remove-stopwords --token-regex "\S+" --input C:\Users\BS\AppData\Local\Temp\5555ca_corpus.txt --output C:\Users\BS\AppData\Local\Temp\5555ca_corpus.mallet' returned non-zero exit status 1.